# Import libraries

In [1]:
import pandas as pd
import numpy as np
from tqdm import tqdm_notebook as tqdm
from emoji import UNICODE_EMOJI
import jieba.posseg as pseg
import jieba
import jieba.analyse
import os
import io

# Load dataset

In [2]:
train_en = pd.read_csv('train_en.csv')
test = pd.read_csv('test.csv')
train_tcn = pd.read_csv('train_tcn.csv')

# Jieba on chinese

Do word embeddings of chinese and english on different categories to map words/translations. 27 for english, 23 for chinese. 7 exactly the same.

In [29]:
a = train_tcn.product_title.apply(lambda x: str(x)).apply(jieba.lcut_for_search)

In [23]:
a

0    [Gucci,  , Gucci,  , Guilty,  , Pour,  , Femme...
1    [（, 二手, ）, PS4,  , GTA,  , 5,  , 俠盜, 獵車, 手, 5,...
2                                              [百獸, 卡]
3                           [nac,  , nac, 活氧全, 效柔, 衣素]
4    [#, Nike, 耐吉, 官方, F, ., C, .,  , 男子, 足球, 長, 褲,...
5    [火影, 忍者, 火影忍者, 六道, 鸣人, cos, 睡衣, 卡卡, 西宇智, 波佐助, ...
6      [第二, 二代, 第二代, 新, 巴克, 史萊姆,  , 210ml,  , 限量, 限量版]
7    [aaL, 皮商旋, ., 全新, 鐵鍋, 上, 五花, 五花肉, 造型, 立體, 冰箱, ...
8    [現貨, 24, 小時, 快速, 出貨, chanel, 香奈兒, 58601, 女包, 經...
9    [【, 拇指, 小拇指, 鞋坊, 】, Adidas,  , Superstar,  , 8...
Name: product_title, dtype: object

In [31]:
#Set of all words present in training
zh_training=set([element for list_ in a.values for element in list_])

In [78]:
#All chinese words present in training and fasttext
temp_zh=df_zh[df_zh.index.isin(zh_training)].index.to_list()

In [80]:
len(temp_zh)

155089

In [79]:
zh_training - set(temp_zh)

{'饃紙',
 '899475',
 '李明泰',
 'INFLUENCER',
 '旋風杯',
 '風格直',
 '夏沙灘',
 '手竿架桿',
 '卡盤',
 '小藍瓶',
 '78GP01',
 '裝書車',
 '興櫃坊',
 '農家樂壁',
 'GAMAKATSU',
 '僅男款',
 '白織',
 '裝沙發',
 '330Ci',
 'ZERIA',
 '潮隱形',
 '艾妮雅',
 '管麥克風',
 '8880192',
 '離心管',
 '沉水馬達',
 '環微',
 '裙速',
 'XHello',
 '兒童理',
 '襪小白襪',
 '朱慧君',
 '挡风玻璃',
 '停產四神',
 '離凝露',
 'TGUCCI',
 '潮媽秋款',
 'Sunnylife',
 '雀點',
 'Dscn8207',
 'X550',
 'GROZ',
 '包高爾夫托',
 'Q5MC1',
 '鐵牛頭',
 '852457',
 '喬盾',
 '全四冊',
 '種針頭',
 '純銀鎖',
 '熱銷貓',
 '眼筆液',
 '劉海碎',
 '宅魚',
 '亮麗桃',
 'WZ5718BY',
 '褲丹寧',
 '素原',
 '8000dpi',
 '車羅伊',
 '西西小鋪',
 '畫鋪',
 'stin',
 '萌洛麗塔',
 '06510',
 '縮片',
 '爐餐',
 '假劉',
 'WX836',
 '陰陽鞋',
 'lnvicta',
 '熱棒燒',
 '867034495',
 'F838',
 '籠貓',
 'ท',
 '恒溫電',
 '套靜',
 'GYQ41Y',
 '清錫渣',
 '舞重',
 'BWSr',
 'GPK01',
 '旅彩條',
 '芭樂雅',
 '商務均',
 '胡芷美肌',
 '贈貓',
 'gucci3D',
 '攜式學',
 '圍後備',
 '棉質圓',
 '鼓剎',
 '帶腳燒',
 '貓專賣',
 '風風口',
 'ysk',
 '套耳',
 '鋼木多層',
 '優惠壓',
 'IMMID',
 'Attack002',
 '視雪紡',
 'BH1001',
 '870022603',
 '離帽',
 'iclub',
 '風雙色',
 '環保口',
 'Dermaspa',
 'B25568',
 '裝拉線',

In [33]:
len(zh_training)

483133

In [45]:
483133-155089

328044

# NLTK on English

Lowercase title, remove emojis, separate words with slash, keep all numbers!

In [55]:
import nltk
from nltk.tokenize import word_tokenize
import re
import string
from itertools import chain

In [248]:
# Pre processing
def preprocess(sample_text):
    sample_text = sample_text.lower() #All lowercase
    sample_text = ('').join([i if i.isalnum() else ' ' for i in sample_text]) # Remove weird characters
    sample_text = sample_text.strip() #Strip
    sample_text = re.sub(' +', ' ', sample_text) #Trim whitespace
    sample_text = (('').join([x for x in sample_text if x not in UNICODE_EMOJI])) # Remove emoji stuck to word
    sample_text = word_tokenize(sample_text) #Word tokenizer
    sample_text = [j for k in [i.split('/') for i in sample_text] for j in k] #Split those joined with /
    sample_text = [x for x in sample_text if x not in UNICODE_EMOJI] #Remove emojis
    sample_text = [''.join(c for c in s if c not in string.punctuation) for s in sample_text] # Remove punctuations
    sample_text = [i for i in sample_text if i!= ''] #Trim extra spaces
#     sample_text = sample_text.translate(str.maketrans("","", string.punctuation))
    return sample_text

In [250]:
sample_text = train_en.iloc[7].product_title
print(sample_text)
a = preprocess(sample_text)
print(a)

【COD】Chanel Black/White Sneaker Shoes For Women
['cod', 'chanel', 'black', 'white', 'sneaker', 'shoes', 'for', 'women']


In [251]:
# Cross check dataframe
en_check = train_en.copy()
en_check['tokenize'] = train_en.product_title.apply(lambda x: preprocess(x))
en_check

product_title  \
0       Recollections Color Splash Clear Stamps & Stencil   
1                               soap,lotion scrub set 400   
2            Spigen Galaxy S10e Case Tough Armor Gunmetal   
3                              Acrylic Lanalon Bright Red   
4                      303 FLAT SHEET/Blanket 100% cotton   
5                                              Korean Set   
6                                     High-grade keychain   
7         【COD】Chanel Black/White Sneaker Shoes For Women   
8                                          Cat eyeglasses   
9       Baby shoes by Stride Rite (BRAND NEW) (3-6 mon...   
10                                     ATI-ATIHAN COSTUME   
11                           Smart lte sim Special number   
12                              FACE MASK NON-WOVEN 50GSM   
13      [OFFICIAL] 2019 BTS 5TH MUSTER (MAGIC SHOP) BL...   
14                                Romoss Sense4 Powerbank   
15      Teal and Light Purple Crystal Dangle Drop Earr...   
16                       ONHAND Sleeveless Crisscross Top   
17        fashion statement necklace \the walking dead\""   
18                                        Rachelle Blouse   
19               SHISEIDO THE COLLAGEN DRINK 50ml(Retail)   
20                            Gummies 500g per pack Php75   
21                                         Ghia Scoopback   
22      Iphone 6 / 6s / 6+ /6s+/ 7 / 7+ / 8 / 8+ Unive...   
23                         Korean ladies strapless skirts   
24                             motor start lowering crown   
25                                             Big Blouse   
26                                      Black Lacey Dress   
27      Eyelash Growth Treatments Makeup Eyelash Enhan...   
28                      COD Hello'Kitty Watch LED (black)   
29                                  CHARLES AND KEITH BAG   
...                                                   ...   
499970                          Castor Oil - COLD PRESSED   
499971   👒AOB: Cross Strap Klipwal Marikina Made Slippers   
499972  8L Electric Deep Fryer 220V Stainless Steel Fr...   
499973                  Elegant Peacock with Studs Brooch   
499974    MN Eyeliner/Eyebrow & Concealer Pencil (2 in 1)   
499975                   Lootbag filler (mini skateboard)   
499976                                   Kahoy  wallpaper   
499977  Authentic Cole Haan Men’s Pinch Weekender PX L...   
499978                 🔥 SALE 🔥 (OF) (AL) TERNO PANTS 041   
499979                                   Peplum pineapple   
499980  Sugar and Spice 100ml Vape Juice E Liquid Vapi...   
499981                Bedsheet  3D semi cotton 4 in 1 set   
499982  Korean Ladies Pure Leather Shinny Vintage Slin...   
499983                   Brilliant Whitening Facial Cream   
499984  amats Folding Table Computer Table Bed Desk No...   
499985                            Mylars  Bundlebags Sale   
499986          Pre-packed 6 sets D&G Top and Candy Pants   
499987           Design realer openwork painting template   
499988  OPPO A9 2020,A5s,A3S,RealmeC2,C3 A31 A33/Neo7 ...   
499989                                          Bow Dress   
499990              PS Vita Game - God Eater 2 Rage Burst   
499991                       COD Chic Style Topshop Dress   
499992                         Colored Stripes Tops ST110   
499993             ForMe REFORME Button Down Shirt (Pink)   
499994                      adapter ulo charger 2in1 2.1A   
499995                       rocker arm roller racing mio   
499996                            Secosana (preloved bag)   
499997                                            jag bag   
499998  Baby wipes 15 sheets (Alcohol and Paraben Free...   
499999                  PRE-LOVED ORIGINAL GREEN FINO BAG   

                          category  \
0             Hobbies & Stationery   
1           Health & Personal Care   
2               Mobile Accessories   
3             Hobbies & Stationery   
4                    Home & Living   
5                  Women's Appare

In [252]:
# Create bag of words from the english training set
bow_en = set(np.hstack(train_en.product_title.apply(lambda x: preprocess(x))))

In [253]:
len(bow_en)

139244

In [254]:
#All chinese words present in training and fasttext
temp_en=df_en[df_en.index.isin(bow_en)].index.to_list()

In [255]:
len(temp_en)

56853

In [289]:
df_en[df_en.index.isin(bow_en)].to_csv('en_embeddings.csv')

In [265]:
en_check[en_check.tokenize.apply(lambda x: 'infiniwhite' in x)]

product_title  \
148883       Infiniwhite BEAUTY CREAM (Whipp Cream) 10g   
271599  Whitening Korean BEAUTY WHIP SET by Infiniwhite   

                      category  \
148883  Health & Personal Care   
271599  Health & Personal Care   

                                                 tokenize  
148883    [infiniwhite, beauty, cream, whipp, cream, 10g]  
271599  [whitening, korean, beauty, whip, set, by, inf...

In [259]:
test = "𝐒𝐄𝐓 𝐂𝐎𝐋𝐋𝐄𝐂𝐓𝐈𝐎𝐍 - Set of 4 Pairs"
test.lower()

'𝐒𝐄𝐓 𝐂𝐎𝐋𝐋𝐄𝐂𝐓𝐈𝐎𝐍 - set of 4 pairs'

In [257]:
# Items in bag of words english that aren't present in en word embed
set(bow_en) - set(temp_en)

{'prijoles',
 'kalea',
 'olavie',
 'cheekers',
 'covel',
 'limecrimes',
 'mk5865',
 'jomalone',
 'heki',
 'longsleves',
 'l252',
 'ginto',
 'av19',
 'w223',
 'pd38',
 'essrntial',
 'bq1525',
 'anastasie',
 'buho',
 '20122194',
 'frshener',
 'lcste',
 'el12',
 '1381g',
 'chynna',
 'zofia',
 'e4020',
 'trinka',
 'necklacewith',
 'michealkors',
 '5moulds',
 'benguet',
 '380629850',
 'sisleyn2',
 'beatter',
 'e5500',
 'topnet',
 'nicholeleebag',
 'k56v',
 '6139237216',
 'elegantrose',
 'wp55',
 'retaso',
 'mr03',
 'jaykensport',
 's2888',
 'rtw37',
 'psre453',
 'db6x',
 'lihgts',
 'jcot',
 'asdasdwqe123',
 '41a1h',
 '196627061',
 'akritax',
 'adolphii',
 'junradvillafrancedignadice',
 'cirtain',
 'snifflease',
 'umaku',
 '1763167625',
 'hongke',
 'giyo',
 '41532',
 'salveo',
 'oppof7',
 'e071',
 '4df',
 '90217',
 'sisyama',
 '3d4390',
 'pw23y',
 '0215205',
 '64x20x15cm',
 'evebaby',
 'leya6677',
 'voltplex',
 'undearmour',
 '60pg',
 '96tabs',
 'yuqiss',
 '4535549570',
 'trhirt',
 'tessel',

In [73]:
train_en[train_en.product_title.str.contains('-')]

product_title  \
6                                     High-grade keychain   
9       Baby shoes by Stride Rite (BRAND NEW) (3-6 mon...   
10                                     ATI-ATIHAN COSTUME   
12                              FACE MASK NON-WOVEN 50GSM   
13      [OFFICIAL] 2019 BTS 5TH MUSTER (MAGIC SHOP) BL...   
30      Pineng PN-968 with LCD Display and Flashlight ...   
32                     4-WAY NURSING / BREASTFEEDING TOPS   
46               Marvel Spider-Man Magazine Issue No.  09   
49      New Casio Gshock GA400 GA-400 Vampire Autoligh...   
50      YFCB-008-2 Multifunctional Motor Mask Camoufla...   
58      For Samsung galaxy Tab A 10.5 SM-T590 T595 Lea...   
64      Children’s Place Sun-glasses for 4-6 Years Old...   
75      Black Skinny Jeans Pants for Men 28-40 Stretch...   
80      Kids New Arrival Tiny Polkadots Layered Mini D...   
84               TEMPTATION - Authentic Victoria's Secret   
89              Life Extension, Gastro-Ease, 60 Vcapsules   
97          Fubu Queens RoundNeck Jersey knits QGT01-0290   
99                         POWER SUPPLY 12V - 5A AC TO DC   
103      Despicable Me 3 Boys’ Flannel 2-pc Sleepwear Set   
108                            US Branded Ladies T-Shirts   
112     KTS-1102 Karaoke Wireless Bluetooth Portable D...   
124                     3pcs 3in1 Baby Turbans 0-36months   
128     KTS-1091 Karaoke Wireless Bluetooth portable L...   
142     HP T0A36AN#140 65 | 2 Ink Cartridges | Black, ...   
154                          Rimshot Drumsticks [T-shirt]   
165               Soft Case VIVO Y91-Y91IC-Y15-S1-V17PRO-   
167     Li-Ion 18350 3.7V 900mAh Nipple Head Lithium I...   
190                         6-12mos Red Tag Baby Leggings   
193     Timing Belt 101T 20mm for Kia Picanto/Getz/Sta...   
195                         Off Shoulder Polka Dress 2-3Y   
...                                                   ...   
499835        2018 Upper Deck Fleer Ultra X-Men Hobby Box   
499838  TATARA Square Nylon Trimmer Line 2.4mm x 15m B...   
499839                       Twilly - Ring Design- PAIR!!   
499843  AC Prints Kids shirt BEN 10 t shirt (boys and ...   
499846                          Korean fashion shoes a-02   
499851  Witch Hazel Rosy Toner (Alcohol-Free Toning Mi...   
499852   Radical Biking Men's Shirt - Cycling Print Black   
499854  Bicycle Lock Anti theft Durable Steel Cable Lo...   
499856                             Branded Women T-shirts   
499861     Plus size34-44  Ladies denim short stretchable   
499866  Shockproof case Samsung A50 A5-2016 A7-2016 E5...   
499870  Versele-Laga Complete Cuni Sensitive Rabbit Fo...   
499893                     ZD-M003 S/S Liquid Thermometer   
499895            Big Necklace w/ Pendant TB-004 , PM-116   
499898               HP 704 Ink Cartridge Black/Tri-Color   
499904                           LED Head Lamp NSS NS-597   
499915  Sun Solon HLJ-606 DC12V Double Headed Vehicle Fan   
499921                Camu Camu Powder - Organic - RETAIL   
499933  Cute Fox Snap Case Matte - Samsung A6s A6+ A7 ...   
499945  MAILTANK IGBT Inverter Welding Machine 305A MM...   
499948          NIA Q8 851s Over-the-Ear Blutooth Headset   
499952  Han Feng illustration bear rabbit Apple 11 mob...   
499961                         DRM Tambourine Double MT-1   
499963  OnlyYouth Men Pale Blue Skinny Jeans (length:3...   
499965                             FCM-69 BALCK MENS BOTA   
499970                          Castor Oil - COLD PRESSED   
499986          Pre-packed 6 sets D&G Top and Candy Pants   
499990              PS Vita Game - God Eater 2 Rage Burst   
499998  Baby wipes 15 sheets (Alcohol and Paraben Free...   
499999                  PRE-LOVED ORIGINAL GREEN FINO BAG   

                          category  
6                    Home & Living  
9                    Babies & Kids  
10               Women Accessories  
12          Health & Personal Care  
13      Toys, Games & Collectibles  
30              Mobile Accessories  
32

In [76]:
en_training=set([element for list_ in a.values for element in list_])

In [81]:
#All chinese words present in training and fasttext
temp_en=df_en[df_en.index.isin(en_training)].index.to_list()

In [97]:
len(temp_en)

99406

In [98]:
len(temp_zh)

155089

# Word embeddings from fasttext

In [35]:
import fasttext
import fasttext.util
import codecs

In [3]:
def load_vectors(embedding_path):
    fin = io.open(embedding_path + '.vec', 'r', encoding='utf-8', newline='\n', errors='ignore')
    n, d = map(int, fin.readline().split())
    print(n,d)
    words = []
    vectors = np.zeros((n,d))
    data = {}
    for idx, line in enumerate(fin):
        tokens = line.rstrip().split(' ')
        words.append(tokens[0])
        vectors[idx,:] += [float(val) for val in tokens[1:]]
#         data[tokens[0]] = map(float, tokens[1:])
        if idx % 10000 == 0:
            print('.', end = ' ')
    np.save(embedding_path + ".npy", vectors)
    with open(embedding_path + ".txt", 'w', encoding='utf-8') as output:
        for row in words:
            output.write(row + '\n')
    return words, vectors

In [11]:
en_words, en_tokens = load_vectors('cc.en.300')

2000000 300
. . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 

In [45]:
zh_words, zh_tokens = load_vectors('cc.zh.300')

2000000 300
. . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . 

In [197]:
import codecs
def load_word_emb_binary(embedding_file_name_w_o_suffix):
    print("Loading binary word embedding from {0}.txt and {0}.npy".format(embedding_file_name_w_o_suffix))

    with codecs.open(embedding_file_name_w_o_suffix + '.txt', 'r', 'utf-8') as f_in:
        index2word = [line.strip() for line in f_in]

    wv = np.load(embedding_file_name_w_o_suffix + '.npy')
    word_embedding_map = {}
    for i, w in enumerate(index2word):
        word_embedding_map[w] = wv[i]

    return word_embedding_map

In [198]:
vec_en = load_word_emb_binary('cc.en.300')

Loading binary word embedding from cc.en.300.txt and cc.en.300.npy


In [199]:
vec_zh = load_word_emb_binary('cc.zh.300')

Loading binary word embedding from cc.zh.300.txt and cc.zh.300.npy


In [200]:
# Load embedding file
zh_tokens = np.load('cc.zh.300.npy')
en_tokens = np.load('cc.en.300.npy')

In [201]:
df_en = pd.DataFrame(vec_en.items(), columns=['words', 'embedding']).set_index('words')
df_zh = pd.DataFrame(vec_zh.items(), columns=['words', 'embedding']).set_index('words')

# Unsupervised learning

In [ ]:
!python unsupervised.py --src_lang zh --tgt_lang en --src_emb cc.zh.300.vec --tgt_emb cc.en.300.vec --n_refinement 5 --normalize_embeddings center

In [ ]:
import os
import pickle

if not os.path.isfile("params.pkl"):
    with open("params.pkl",'wb') as file:
        pickle.dump(, file)

# Getting nearest neighbor

In [58]:
def get_w2v(sentence, model):
    """
    :param sentence: inputs a single sentences whose word embedding is to be extracted.
    :param model: inputs glove model.
    :return: returns numpy array containing word embedding of all words    in input sentence.
    """
    return np.array([model.get(val, np.zeros(100)) for val in sentence.split()], dtype=np.float64)

In [198]:
def get_nn(word, src_emb, tgt_emb, df_tgt, K=5):
    print("Nearest neighbors of \"%s\":" % word)
    word_emb = get_w2v(word, src_emb).T
    scores = (tgt_emb / np.linalg.norm(tgt_emb, 2, 1)[:, None]).dot(word_emb / np.linalg.norm(word_emb))
    k_best = scores.reshape(1,-1)[0].argsort()[-5:][::-1]
    for i, idx in enumerate(k_best):
        print('%.4f - %s' % (scores[idx], df_tgt.iloc[idx].name))

In [201]:
df_zh[df_zh.index == '貓']

embedding
words                                                   
貓      [-0.2967, 0.0171, 0.4615, 0.3601, 0.0896, -0.2...

In [206]:
get_nn('booty', vec_en, en_tokens, df_en)

Nearest neighbors of "booty":
1.0000 - booty
0.7237 - booty.
0.6722 - bootys
0.6376 - bootay
0.6169 - Booty


In [153]:
test_scores[270830]

array([0.25989007])

In [142]:
test_scores.reshape(1,-1).argsort()[-5:][::-1]

array([[ 32690, 615543, 413467, ..., 368506, 960130, 270830]], dtype=int64)

In [130]:
test_scores.argsort()[-5:][::-1]

array([[0],
       [0],
       [0],
       [0],
       [0]], dtype=int64)

In [162]:
list(vec_en.keys())

{'，': array([ 8.000e-03,  3.360e-02,  5.720e-01, -1.105e-01, -2.000e-02,
         1.950e-02, -1.290e-02, -2.580e-02,  2.490e-02, -1.000e-03,
         1.820e-02, -7.400e-03, -2.880e-02, -1.160e-02, -3.550e-02,
         4.820e-02,  4.110e-02,  8.000e-04,  2.610e-02, -3.870e-02,
         1.040e-02, -3.500e-03,  7.150e-02, -1.000e-04, -3.970e-02,
        -3.530e-02,  5.460e-02, -4.620e-02, -4.390e-02,  6.210e-02,
        -2.760e-02,  1.510e-02, -5.280e-02, -1.600e-03,  7.400e-03,
        -3.120e-02,  3.200e-03, -8.430e-02, -6.980e-02, -3.090e-02,
         1.780e-02,  8.100e-03, -2.030e-02,  1.040e-02, -1.739e-01,
        -8.100e-03, -9.520e-02, -1.180e-02,  2.110e-02,  2.140e-02,
        -3.240e-02,  8.500e-03, -1.140e-02, -4.785e-01, -2.160e-02,
         4.690e-02, -2.600e-03,  1.520e-02, -4.380e-02,  5.540e-02,
        -4.410e-02, -2.560e-02, -8.400e-03, -1.210e-02, -3.720e-02,
        -1.090e-02,  7.040e-02,  2.080e-02, -4.570e-02, -2.520e-02,
        -1.150e-02,  4.140e-02,  7.800e-03,

In [156]:
k_best = test_scores.reshape(1,-1)[0].argsort()[-5:][::-1]
for i, idx in enumerate(k_best):
    print(idx)
#     print('%.4f - %s' % (scores[idx], tgt_id2word[idx]))

270830
960130
368506
555694
97995


In [113]:
get_nn('cat', vec_en, zh_tokens)

Nearest neighbors of "cat":


array([[0],
       [0],
       [0],
       [0],
       [0]], dtype=int64)

In [96]:
word_emb = test
(vec_zh / np.linalg.norm(vec_zh, 2, 1)[:, None]).dot(word_emb / np.linalg.norm(word_emb))

AttributeError: 'dict' object has no attribute 'conjugate'

In [105]:
word_emb = test.T
(zh_tokens / np.linalg.norm(zh_tokens, 2, 1)[:, None]).dot(word_emb / np.linalg.norm(word_emb))

array([[-0.02646693],
       [-0.00920756],
       [-0.01300759],
       ...,
       [-0.00100558],
       [-0.04740634],
       [ 0.01967714]])

In [82]:
np.linalg.norm(tgt_emb.values(), 2, 1)

AttributeError: 'dict_values' object has no attribute 'conjugate'

In [79]:
tgt_emb = vec_zh
(tgt_emb / np.linalg.norm(tgt_emb, 2, 1)[:, None])

AttributeError: 'dict' object has no attribute 'conjugate'

In [69]:
test = get_w2v('bleh', vec_en)

In [ ]:
# printing nearest neighbors in the target space
src_word = 'cat'
get_nn(src_word, src_embeddings, src_id2word, tgt_embeddings, tgt_id2word, K=5)